<a href="https://colab.research.google.com/github/maiaufrrj/BRtrading/blob/main/Long_Target.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#! pip install pycaret --upgrade pandas --upgrade
#! pip install sweetviz

In [1]:
import numpy as np
import pickle
import pandas as pd
from datetime import datetime
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split, TimeSeriesSplit
from pycaret.classification import *
from google.colab import drive
import warnings
warnings.filterwarnings("ignore")

In [ ]:
drive.mount('/content/drive')

In [18]:
filename = '/content/drive/MyDrive/ColabNotebooks/datasets/trading/EURUSD_h1.pkl'
df = pickle.load(open(filename, 'rb'))

In [19]:
print('início do dataset: '+ str(df.index[1]))
print('final do dataset: '+ str(df.index[-1]))

início do dataset: 2005-09-07 00:00:00
final do dataset: 2021-10-29 23:00:00


<h2>Separando datasets<br>
<h5> df_train: utilizado no treino e validações cruzadas<br>
<h5> df_valid: utilizado após os testes para validação final<br>

In [20]:
separar=6500 #separando 6500hs para validação (01-01-2021 --> 29-10-2021 23:00)

#dataset utilizado para treino e validações cruzadas
df_train = df.iloc[:-(separar-1),:]

#dataset utilizado após os testes para validação final
df_valid = df.iloc[-separar:,:]

In [21]:
df_train.shape

(93500, 7)

<h2>Análise Exploratória<br>
<h5>Histograma para cada passo à frente (definindo alvos)

In [22]:
#função para verificar variação para n passos à frente
def Delta(DF,n):
    '''Busca os n valores à frente'''
    df = DF.copy()
    for i in n:
      name='delta'+str(i)
      df[name] = 100*((df['close'].shift(-i) - df['close'])/df['close'])
      df.dropna(inplace=True)
    
    del df['open'],df['high'],df['low'],df['tick_volume'],df['spread'],df['real_volume']
    return df

lista_forecast=list(range(1,13))
df_analise = Delta(df_train,lista_forecast)

In [ ]:
import sweetviz as sv
#Gerar relatório do Sweetviz
report = sv.analyze(df_analise)
report.show_html("/content/drive/MyDrive/ColabNotebooks/datasets/trading/Analise_EURUSD.html")

In [23]:
alvo=0.38
delta=6

In [24]:
df_analise[df_analise > alvo].count()
coluna='delta'+str(delta)
print('Percentual maior que o alvo('+str(alvo) + '%) em delta('+str(delta)+') = {:.2f}'.format(100*(df_analise[coluna][df_analise[coluna] > alvo].count()/93500))+'%')

Percentual maior que o alvo(0.38%) em delta(6) = 7.02%


In [ ]:
import plotly.express as px
import plotly.graph_objects as go

fig = px.histogram(df, x=df_analise[coluna], nbins=100, histnorm='percent')
fig.show()

#histograma de variação de 12 passos à frente
coluna2='delta12'
fig = px.histogram(df, x=df_analise[coluna2], nbins=100, histnorm='percent')
fig.show()

<h2>Criando Features<br>

In [25]:
#criar feature ADF

def MediaMovelSimples(DF,n):
    ''' função para calcular Média Móvel ---indicador de tendência'''
    df = DF.copy()
    name='MM'+ str(n)  
    df[name] = df['close'].rolling(window=n, min_periods=1).mean()
    df.dropna(inplace=True) 
    return df
    
def DesvioPadrao(DF,n):
    ''' função para calcular Desvio Padrão ---indicador de volatilidade'''
    df = DF.copy()
    name='STD'+ str(n)
    df[name] = df['close'].rolling(window=n, min_periods=1).std()
    df.dropna(inplace=True)  
    return df

def MediaMovelExponcial(DF,n):
    ''' função para calcular Média Móvel Exponencial ------indicador de tendência'''
    df = DF.copy()
    name='EWM'+ str(n)
    df[name] = df['close'].ewm(span=n).mean()
    df.dropna(inplace=True) 
    return df
    
def ATR(DF,n):
    '''função para calcular TR e ATR ---indicadores de volatilidade'''    
    df = DF.copy()
    name1='ATR'+ str(n)
    name2='TR' + str(n)
    df['H-L'] = abs(df['high']-df['low'])
    df['H-PC']= abs(df['high']-df['close'].shift(1))
    df['L-PC']=abs(df['low']-df['close'].shift(1))
    df[name2]=  df[['H-L','H-PC', 'L-PC']].max(axis=1,skipna=False)
    df[name1]= df[name2].rolling(n).mean()
    df = df.drop(['H-L','H-PC', 'L-PC'],axis=1)
    df.dropna(inplace=True) 
    return df
  
def BollBnd(DF,n):
    '''função para calcular Bandas de Bollinger ---indicador de tendência''' 
    df = DF.copy()
    name1='BBsup'+ str(n)
    name2='BBinf'+ str(n)
    name3='BBlarg'+ str(n)
    df['MA'] = df['close'].rolling(n).mean()
    df[name1] = df['MA'] + 2*df['MA'].rolling(n).std()
    df[name2] = df['MA'] - 2*df['MA'].rolling(n).std()
    df[name3] = df[name1]-df[name2]
    df = df.drop(['MA'],axis=1)
    df.dropna(inplace=True)
    return df

def RSI(DF,n):
    '''função para calcular RSI (Índice de Força Relativa) ---indicador de tendência''' 
    df = DF.copy()
    name='RSI'+ str(n)
    df['delta'] = df['close'] - df['close'].shift(1)
    df['gain'] = np.where(df['delta']>=0,df['delta'],0)
    df['loss'] = np.where(df['delta']<0,abs(df['delta']),0)
    avg_gain = [] 
    avg_loss = []
    gain = df['gain'].tolist()
    loss= df['loss'].tolist()
    for i in range(len(df)):
        if i < n:
            avg_gain.append(np.NaN)
            avg_loss.append(np.NaN)
        elif i==n:
            avg_gain.append(df['gain'].rolling(n).mean().tolist()[n])
            avg_loss.append(df['loss'].rolling(n).mean().tolist()[n])
        elif i>n:
            avg_gain.append(((n-1)*avg_gain[i-1]+gain[i])/n)
            avg_loss.append(((n-1)*avg_loss[i-1]+loss[i])/n)   
    
    df['avg_gain']=np.array(avg_gain)
    df['avg_loss']=np.array(avg_loss)
    df['RS']=df['avg_gain']/df['avg_loss']
    df[name]=100-(100/(1+df['RS']))
    df = df.drop(['delta','avg_gain','avg_loss','loss','gain','RS'],axis=1)
    df.dropna(inplace=True)  
    return df

   
def nIndicadores(DF,n):
    df=DF.copy()
    df = MediaMovelSimples(df,n)
    df = DesvioPadrao(df,n)
    df = MediaMovelExponcial(df,n)
    df = ATR(df,n)
    df = BollBnd(df,n)
    df = RSI(df,n)
    return df

#lista=[3,5,7,9,24,50,120] #otimizar essa sequência
#usando sequência de Fibonacci
lista=[3, 5, 8, 13, 21, 34, 55, 89, 144]

for n in lista:
    df_train=nIndicadores(df_train,n)

Anotações

In [ ]:
#def Forecast(DF,n):
#    '''Busca os n preços de fechamento a frente'''
#    df = DF.copy()
#    df['y']=df['close'].shift(-n)
#    df.dropna(inplace=True)
#    return df

#def movimento_alta(DF,n,percentual_alta):
#    '''Verifica se o preço de fechamento n períodos a frente é maior que um certo limite percentual (alta)'''
#    df = DF.copy()
#    df['delta'] = (df['close'].shift(-n) - df['close'])/df['close']
#    df['alta'] = np.where(df['delta']>=percentual_alta,1,0)
#    df = df.drop(['delta'],axis=1)
#    df.dropna(inplace=True)  
#    return df

#def low_target(DF,n,percentual_baixa):
    '''Verifica se o preço de fechamento n períodos a frente é menor que um certo limite percentual (alta)'''
#    df = DF.copy()
#    df['delta'] = (df['close'].shift(-n) - df['close'])/df['close']
#    df['baixa'] = np.where(df['delta']<=-percentual_baixa,1,0)
#    df = df.drop(['delta'],axis=1)
#    df.dropna(inplace=True)  
#    return df

#def low_target(DF, baixa_esperada, periodos_frente):
#    '''avalia n períodos à frente, se o valor máximo atinge a alta_esperada'''
#    df = DF.copy()

#    '''cria n colunas delta, uma para cada período a frente e calcula a diferença entre fechamento futuro e atual'''
#    for i in range(periodos_frente):
#      name='delta'+str(i)
#      df[name] = (df['close'].shift(-i) - df['close'])/df['close']
#
#    for i in range(periodos_frente):
#      df['baixa'] = np.where(df['delta'+str(i)]<=-baixa_esperada,1,0)
    
#    for i in range(periodos_frente):
#      name='delta'+str(i)
#      df = df.drop([name],axis=1)
  
#    df.dropna(inplace=True)
#    return df

#def low_target(DF, baixa_esperada, periodos_frente):
#    '''avalia n períodos à frente, se o valor máximo atinge a alta_esperada'''
#    df = DF.copy()

#    '''cria n colunas delta, uma para cada período a frente e calcula a diferença entre fechamento futuro e atual'''
#    for i in range(periodos_frente):
#      name='delta_close'+str(i)
#      df[name] = (df['close'].shift(-i) - df['close'])/df['close']
#      name='delta_low'+str(i)
#      df[name] = (df['low'].shift(-i) - df['close'])/df['close']
#      name='delta_high'+str(i)
#      df[name] = (df['high'].shift(-i) - df['close'])/df['close']

#    for i in range(periodos_frente):
#      df['baixa'] = np.where((df['delta_close'+str(i)]<=-baixa_esperada) | (df['delta_low'+str(i)]<=-baixa_esperada) | (df['delta_high'+str(i)]<=-baixa_esperada), 1, 0)
    
#    for i in range(periodos_frente):
#      name1='delta_close'+str(i)
#      name2='delta_low'+str(i)
#      name3='delta_high'+str(i)
#      df = df.drop([name1,name2,name3],axis=1)

#    df.dropna(inplace=True)
#    return df

<h2>Criando Targets<br>
<h5> LongTarget: <br>
verificar se há chance de aumento de preço n períodos à frente (sinal de compra)<br>

In [26]:
def low_target(DF, baixa_esperada, periodos_frente):
    '''avalia n períodos à frente, se o valor máximo atinge a alta_esperada'''
    df = DF.copy()
    df['baixa'] = 0
    '''cria n colunas delta, uma para cada período a frente e calcula a diferença entre fechamento futuro e atual'''
    for i in range(1,periodos_frente+1):
      name='delta_close'+str(i)
      df[name] = (df['close'].shift(-i) - df['close'])/df['close']

    for i in range(1,periodos_frente+1):
      df['baixa'+str(i)] = np.where(df['delta_close'+str(i)]<=-baixa_esperada,1,0)
    
    for i in range(1,periodos_frente+1):
      df['baixa'] = df['baixa'] + df['baixa'+str(i)]

    #trocando sinais aqui!!!
    df['baixa'] = np.where(df['baixa']>=1,1,0)

    for i in range(1,periodos_frente+1):
      name1='delta_close'+str(i)
      name2='baixa'+str(i)
      df = df.drop([name1,name2],axis=1)
      
    df.dropna(inplace=True)
    return df

def high_target(DF, alta_esperada, periodos_frente):
    '''avalia n períodos à frente, se o valor máximo atinge a alta_esperada'''
    df = DF.copy()
    df['high_target'] = 0

    '''cria n colunas delta, uma para cada período a frente e calcula a diferença entre fechamento futuro e atual'''
    for i in range(1,periodos_frente+1):
      name='delta_close'+str(i)
      df[name] = (df['close'].shift(-i) - df['close'])/df['close']

    for i in range(1,periodos_frente+1):
      #df['high_target'] = np.where((df['delta_close'+str(i)]>=alta_esperada) | (df['delta_low'+str(i)]>=alta_esperada) | (df['delta_high'+str(i)]>=alta_esperada), 1, 0)
      df['high_target'+str(i)] = np.where(df['delta_close'+str(i)]>=alta_esperada,1,0)

    for i in range(1,periodos_frente+1):
      df['high_target'] = df['high_target'] + df['high_target'+str(i)]
    
    df['high_target'] = np.where(df['high_target']>=1,1,0)

    for i in range(1,periodos_frente+1):
      name1='delta_close'+str(i)
      name2='high_target'+str(i)
      df = df.drop([name1,name2],axis=1)

    df.dropna(inplace=True)
    return df

In [27]:
#Usar em caso de low_target
#baixa_esperada = 0.004
#df = low_target(df,baixa_esperada,6)

percentual_alta = alvo/100
alta_esperada = alvo/100
df_train = high_target(df_train,alta_esperada,6) #target

#definindo o target = df['high_target']
df_train['y']=df_train['high_target']
del df_train['high_target'], df_train['tick_volume'], df_train['spread'], df_train['real_volume'], df_train['open'], df_train['high'], df_train['low']

In [28]:
df_train.head()

close       MM3      STD3      EWM3     TR3      ATR3  \
time                                                                          
2005-12-01 14:00:00  1.1733  1.175333  0.001818  1.175013  0.0048  0.003800   
2005-12-01 15:00:00  1.1706  1.173267  0.002650  1.172807  0.0034  0.003933   
2005-12-01 16:00:00  1.1711  1.171667  0.001436  1.171953  0.0030  0.003733   
2005-12-01 17:00:00  1.1702  1.170633  0.000451  1.171077  0.0031  0.003167   
2005-12-01 18:00:00  1.1711  1.170800  0.000520  1.171088  0.0026  0.002900   

                       BBsup3    BBinf3   BBlarg3       RSI3      MM5  \
time                                                                    
2005-12-01 14:00:00  1.177916  1.172751  0.005165   2.576077  1.17656   
2005-12-01 15:00:00  1.177039  1.169494  0.007545   1.290660  1.17500   
2005-12-01 16:00:00  1.175343  1.167990  0.007353  13.306865  1.17354   
2005-12-01 17:00:00  1.173287  1.167980  0.005307  10.015104  1.17222   
2005-12-01 18:00:00  1.171910  1.169690  0.002219  34.368361  1.17126   

                         STD5      EWM5     TR5     ATR5    BBsup5    BBinf5  \
time                                                                           
2005-12-01 14:00:00  0.002115  1.175871  0.0048  0.00284  1.177899  1.175221   
2005-12-01 15:00:00  0.003077  1.174114  0.0034  0.00316  1.177580  1.172420   
2005-12-01 16:00:00  0.002777  1.173109  0.0030  0.00356  1.177172  1.169908   
2005-12-01 17:00:00  0.002381  1.172140  0.0031  0.00358  1.176514  1.167926   
2005-12-01 18:00:00  0.001201  1.171793  0.0026  0.00338  1.175507  1.167013   

                      BBlarg5       RSI5       MM8      STD8      EWM8  \
time                                                                     
2005-12-01 14:00:00  0.002677   6.103980  1.177113  0.001772  1.176579   
2005-12-01 15:00:00  0.005161   3.613504  1.176175  0.002838  1.175251   
2005-12-01 16:00:00  0.007264  11.931279  1.175300  0.003214  1.174328   
2005-12-01 17:00:00  0.008587   9.991306  1.174338  0.003467  1.173411   
2005-12-01 18:00:00  0.008494  25.195008  1.173425  0.003195  1.172897   

                        TR8      ATR8    BBsup8    BBinf8   BBlarg8  \
time                                                                  
2005-12-01 14:00:00  0.0048  0.002275  1.178075  1.176150  0.001925   
2005-12-01 15:00:00  0.0034  0.002537  1.177723  1.174627  0.003097   
2005-12-01 16:00:00  0.0030  0.002725  1.177520  1.173080  0.004440   
2005-12-01 17:00:00  0.0031  0.002962  1.177277  1.171398  0.005878   
2005-12-01 18:00:00  0.0026  0.003062  1.176994  1.169856  0.007138   

                          RSI8      MM13     STD13     EWM13    TR13  \
time                                                                   
2005-12-01 14:00:00  12.646811  1.177623  0.001523  1.177181  0.0048   
2005-12-01 15:00:00   8.427199  1.177008  0.002437  1.176241  0.0034   
2005-12-01 16:00:00  14.467010  1.176415  0.002864  1.175507  0.0030   
2005-12-01 17:00:00  12.738613  1.175769  0.003251  1.174749  0.0031   
2005-12-01 18:00:00  23.221826  1.175231  0.003409  1.174227  0.0026   

                        ATR13   BBsup13   BBinf13  BBlarg13      RSI13  \
time                                                                     
2005-12-01 14:00:00  0.001877  1.178354  1.176892  0.001463  22.824117   
2005-12-01 15:00:00  0.002038  1.178135  1.175880  0.002255  17.163763   
2005-12-01 16:00:00  0.002177  1.177977  1.174853  0.003124  21.089772   
2005-12-01 17:00:00  0.002292  1.177786  1.173753  0.004033  19.305554   
2005-12-01 18:00:00  0.002400  1.177688  1.172774  0.004914  26.080374   

                         MM21     STD21     EWM21    TR21     ATR21   BBsup21  \
time                                                                            
2005-12-01 14:00:00  1.178157  0.001387  1.177622  0.0048  0.001771  1.178543   
2005-12-01 15:00:00  1.177771  0.002146  1.176984  0.0034  0.001852  1.178183   
2005-12-01 16:00:00  1.177414 

In [ ]:
#workbook='/content/drive/MyDrive/ColabNotebooks/datasets/trading/dataframe_eurusd.xlsx'
#df.to_excel(workbook)

In [29]:
X= df_train.iloc[:,:-1]  #da primeira à penultima (variáveis dependentes)
y= df_train.iloc[:,-1]    #ultima coluna (dados de previsão)

In [38]:
#balanceamento SMOTE
exp_clf = setup(df_train,
                target = 'y', 
                fold_strategy = 'timeseries',
                fold = 15,
                train_size=0.7,
                feature_selection = True,
                fix_imbalance = True,
                #feature_selection_threshold = 0.70,  '''para long_target '''
                feature_selection_threshold = 0.70,
                remove_multicollinearity = True,
                multicollinearity_threshold = 0.80,
                remove_perfect_collinearity = True,
                normalize = True,
                n_jobs=-1,
                session_id = 123)

Description             Value
0                               session_id               123
1                                   Target                 y
2                              Target Type            Binary
3                            Label Encoded              None
4                            Original Data       (92021, 83)
5                           Missing Values             False
6                         Numeric Features                82
7                     Categorical Features                 0
8                         Ordinal Features             False
9                High Cardinality Features             False
10                 High Cardinality Method              None
11                   Transformed Train Set        (64414, 9)
12                    Transformed Test Set        (27607, 9)
13                      Shuffle Train-Test              True
14                     Stratify Train-Test             False
15                          Fold Generator   TimeSeriesSplit
16                             Fold Number                15
17                                CPU Jobs                -1
18                                 Use GPU             False
19                          Log Experiment             False
20                         Experiment Name  clf-default-name
21                                     USI              43cd
22                         Imputation Type            simple
23          Iterative Imputation Iteration              None
24                         Numeric Imputer              mean
25      Iterative Imputation Numeric Model              None
26                     Categorical Imputer          constant
27  Iterative Imputation Categorical Model              None
28           Unknown Categoricals Handling    least_frequent
29                               Normalize              True
30                        Normalize Method            zscore
31                          Transformation             False
32                   Transformation Method              None
33                                     PCA             False
34                              PCA Method              None
35                          PCA Components              None
36                     Ignore Low Variance             False
37                     Combine Rare Levels             False
38                    Rare Level Threshold              None
39                         Numeric Binning             False
40                         Remove Outliers             False
41                      Outliers Threshold              None
42                Remove Multicollinearity              True
43             Multicollinearity Threshold               0.8
44             Remove Perfect Collinearity              True
45                              Clustering             False
46                    Clustering Iteration              None
47                     Polynomial Features             False
48                       Polynomial Degree              None
49                    Trignometry Features             False
50                    Polynomial Threshold              None
51                          Group Features             False
52                       Feature Selection              True
53                Feature Selection Method           classic
54            Features Selection Threshold               0.7
55                     Feature Interaction             False
56                           Feature Ratio             False
57                   Interaction Threshold              None
58                           Fix Imbalance              True
59                    Fix Imbalance Method             SMOTE

In [34]:
best = compare_models(sort = 'MCC', include = ['et','lightgbm','rf'])

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.8910  0.7734  0.2827  0.4034   
rf               Random Forest Classifier    0.8656  0.7552  0.3386  0.3140   
lightgbm  Light Gradient Boosting Machine    0.7003  0.7156  0.5870  0.1775   

              F1   Kappa     MCC  TT (Sec)  
et        0.3322  0.2748  0.2801     6.583  
rf        0.3257  0.2512  0.2514    18.860  
lightgbm  0.2717  0.1467  0.1894     0.856

In [ ]:
#criando modelos
model = create_model('et')
model_tuned = tune_model(estimator = model,  fold = 15,  round = 4,  n_iter = 100,  optimize = 'MCC', verbose = True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.8693  0.6792  0.1443  0.2327  0.1781  0.1114  0.1151
1       0.8760  0.7241  0.2044  0.2660  0.2311  0.1650  0.1667
2       0.8763  0.7325  0.2294  0.3090  0.2633  0.1974  0.2000
3       0.8817  0.7397  0.2487  0.3587  0.2938  0.2315  0.2362
4       0.8880  0.7420  0.2732  0.3679  0.3135  0.2540  0.2573
5       0.8837  0.7503  0.2711  0.3668  0.3118  0.2498  0.2532
6       0.8872  0.7714  0.2655  0.4038  0.3204  0.2617  0.2686
7       0.8917  0.7839  0.3027  0.3862  0.3394  0.2813  0.2838
8       0.8892  0.7936  0.2741  0.4221  0.3323  0.2749  0.2825
9       0.8947  0.8036  0.2884  0.4129  0.3396  0.2843  0.2897
10      0.9016  0.8101  0.3021  0.4556  0.3633  0.3124  0.3202
11      0.8944  0.8072  0.3488  0.4751  0.4023  0.3458  0.3508
12      0.9004  0.8106  0.3429  0.4662  0.3952  0.3423  0.3471
13      0.9016  0.8089  0.3247  0.4789  0.3870  0.3356  0.3432
14      0.9068  0.8175  0.3181  0.4917  0.3863  0.3383  0.3478
Mean    0.8895  0.7716  0.2759  0.3929  0.3238  0.2657  0.2708
SD      0.0104  0.0401  0.0523  0.0757  0.0610  0.0661  0.0675

IntProgress(value=0, description='Processing: ', max=7)

Initiated  . . . . . . . . . . . . . . . . . .                   00:24:36
Status     . . . . . . . . . . . . . . . . . .  Searching Hyperparameters
Estimator  . . . . . . . . . . . . . . . . . .     Extra Trees Classifier

Empty DataFrame
Columns: [Accuracy, AUC, Recall, Prec., F1, Kappa, MCC]
Index: []

Fitting 15 folds for each of 100 candidates, totalling 1500 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 196 tasks      | elapsed: 10.6min
[Parallel(n_jobs=-1)]: Done 446 tasks      | elapsed: 18.3min


In [ ]:
model_tuned

ExtraTreesClassifier(bootstrap=True, ccp_alpha=0.0, class_weight={},
                     criterion='gini', max_depth=11, max_features=1.0,
                     max_leaf_nodes=None, max_samples=None,
                     min_impurity_decrease=0, min_impurity_split=None,
                     min_samples_leaf=4, min_samples_split=10,
                     min_weight_fraction_leaf=0.0, n_estimators=140, n_jobs=-1,
                     oob_score=False, random_state=123, verbose=0,
                     warm_start=False)

In [ ]:
evaluate_model(model_tuned)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Hyperparameters', 'param…

In [ ]:
#avaliar modelo

# generate predictions on the original dataset
predictions_df = predict_model(model_tuned, data=df_train)
predictions_df = predictions_df.reset_index()


#'matriz de confusão avaliando n itens à frente'

#def evaluate_pred(DF, alta_esperada, periodos_frente):
        
#    df = DF.copy()
#    df['evaluate_pred'] = 0

#    '''cria n colunas delta, uma para cada período a frente e calcula a diferença entre fechamento futuro e atual'''
#    for i in range(1,periodos_frente+1):
#      name='delta_close'+str(i)
#      if df[df['Label']]==1:
#        df[name] = (df['close'].shift(-i) - df['close'])/df['close']
    
#    for i in range(1,periodos_frente+1):
#      df['evaluate_pred'+str(i)] = np.where(df['delta_close'+str(i)]>=alta_esperada,1,0)

#    for i in range(1,periodos_frente+1):
#      df['evaluate_pred'] = df['evaluate_pred'] + df['evaluate_pred'+str(i)]
    
    #df['evaluate_pred'] = np.where(df['evaluate_pred']>=1,1,0)

#    for i in range(1,periodos_frente+1):
#      name1='delta_close'+str(i)
#      name2='evaluate_pred'+str(i)
#      df = df.drop([name1,name2],axis=1)

#    df.dropna(inplace=True)
#    return df


#percentual_alta = 0.004
#alta_esperada = 0.004
#eval = evaluate_pred(df_train,alta_esperada,6) #target


#y_pred=predictions_df['Label']
#y_pred = pd.DataFrame(y_pred)
#y_pred.set_index(df_train.index, inplace=True)
#y_true = df_train['y']

#from sklearn.metrics import plot_confusion_matrix
#confusion_matrix(y_true, y_pred)

'matriz de confusão avaliando n itens à frente'

In [ ]:
eval.evaluate_pred.value_counts()


In [ ]:
predictions_df.head(10)

In [ ]:
#finalize a model
final_model = finalize_model(model_tuned)
save_model(final_model, '/content/drive/MyDrive/ColabNotebooks/datasets/trading/modelos/long_target_et')

Transformation Pipeline and Model Successfully Saved


(Pipeline(memory=None,
          steps=[('dtypes',
                  DataTypes_Auto_infer(categorical_features=[],
                                       display_types=True, features_todrop=[],
                                       id_columns=[],
                                       ml_usecase='classification',
                                       numerical_features=[], target='y',
                                       time_features=[])),
                 ('imputer',
                  Simple_Imputer(categorical_strategy='not_available',
                                 fill_value_categorical=None,
                                 fill_value_numerical=None,
                                 numeric_strategy='...
                  ExtraTreesClassifier(bootstrap=True, ccp_alpha=0.0,
                                       class_weight={}, criterion='gini',
                                       max_depth=11, max_features=1.0,
                                       max_leaf_nodes=None,

In [ ]:
#salvando modelo
#import pickle
#filename = '/content/drive/MyDrive/ColabNotebooks/datasets/trading/modelos/et_tuned01.pkl'
#pickle.dump(final_model, open(filename, 'wb'))

In [ ]:
#importando modelo short_target_et
short_target = load_model('/content/drive/MyDrive/ColabNotebooks/datasets/trading/modelos/short_target_et')

Transformation Pipeline and Model Successfully Loaded


In [ ]:
#importando df_train usado pra ajustar o outro indicador
file = open("/content/drive/MyDrive/ColabNotebooks/datasets/trading/modelos/df_train_short_target.pkl",'rb')
df_train_short_target = pickle.load(file)
file.close()

#importando df_valid do outro indicador
file = open('/content/drive/MyDrive/ColabNotebooks/datasets/trading/modelos/df_valid_short_target.pkl','rb')
df_valid_short_target = pickle.load(file)
file.close()

In [ ]:
# generate predictions on the original dataset
predictions_df = predict_model(final_model, data=df_train)
predictions_df = predictions_df.reset_index()

#previsão com modelo short_target
#predictions_short_target = predict_model(short_target, data=df_train_short_target)
#predictions_short_target = predictions_short_target.reset_index()

def alinhar_pontos(DF):
    '''cria uma coluna, em que o valor da Label será igual ao close*(1+percentual_alta) caso Label=1 '''
    df = DF.copy()
    df['Label'] = np.where(df['Label']==1,df['close'],0)
    #df['high_target'] = np.where(df['baixa']==1,df['close'],0)
    return df

predictions_df = alinhar_pontos(predictions_df)
#predictions_short_target = alinhar_pontos(predictions_short_target)

In [ ]:
# line plot
import plotly.express as px
import plotly.graph_objects as go
fig = px.line(predictions_df, x='time', y='close', template = 'plotly_dark')

#fig = go.Figure(data=[go.Candlestick(x=predictions_df['time'],
#                open=predictions_df['open'],
#                high=predictions_df['high'],
#                low=predictions_df['low'],
#                close=predictions_df['close'])])

fig.add_scatter(x=predictions_df['time'], y=predictions_df['Label'], mode='markers', marker_color='rgba(0, 255, 0, .8)')
#fig.add_scatter(x=predictions_short_target['time'], y=predictions_short_target['Label'], mode='markers', marker_color='rgba(255, 0, 0, .8)')
#fig.add_scatter(x=predictions_df_teste['time'], y=predictions_df_teste['baixa'], mode='markers', marker_color='rgba(255, 0, 0, .8)')

ymin=predictions_df.close.min()
ymax=predictions_df.close.max()
fig.update_yaxes(range=[ymin, ymax])
fig.show()
fig.write_html('/content/drive/MyDrive/ColabNotebooks/datasets/trading/modelos/long_target_et.html')

Em que horários os indicadores performam bem?

In [ ]:
#! pip install backtrader

In [ ]:
df_valid.head()

In [ ]:
#criando featues para df_valid
lista=[3, 5, 8, 13, 21, 34, 55, 89, 144]

df_valid_eval = df_valid.copy()
for n in lista:
    df_valid_eval=nIndicadores(df_valid_eval,n)

#Usar em caso de low_target
#baixa_esperada = 0.004
#df = low_target(df,baixa_esperada,6)

percentual_alta = alvo/100
alta_esperada = alvo/100
#df_valid_eval = high_target(df_valid_eval,alta_esperada,6) #target

#definindo o target = df['high_target']
#df_valid_eval['y']=df_valid_eval['high_target']
#del df_valid_eval['high_target'] 
del df_valid_eval['tick_volume'], df_valid_eval['spread'], df_valid_eval['real_volume']	

In [ ]:
df_valid_eval.shape

(5021, 85)

In [ ]:
# testando dados no dataset de validação
predictions_df_teste = predict_model(model_tuned, data=df_valid_eval)
predictions_df_teste = predictions_df_teste.reset_index()

#predictions_short_target_teste = predict_model(short_target, data=df_valid_short_target)
#predictions_short_target_teste = predictions_short_target_teste.reset_index()

In [ ]:
def alinhar_pontos(DF):
    '''cria uma coluna, em que o valor da Label será igual ao close*(1+percentual_alta) caso Label=1 '''
    df = DF.copy()
    df['Label'] = np.where(df['Label']==1,df['close'],0)
    #df = df.drop(['delta'],axis=1)
    #df.dropna(inplace=True)  
    return df

predictions_df_teste = alinhar_pontos(predictions_df_teste)
#predictions_short_target_teste = alinhar_pontos(predictions_short_target_teste)

In [ ]:
import plotly.express as px
import plotly.graph_objects as go
fig = px.line(predictions_df_teste, x='time', y='close', template = 'plotly_dark')

fig.add_scatter(x=predictions_df_teste['time'], y=predictions_df_teste['Label'], mode='markers', marker_color='rgba(0, 255, 0, .8)')
#fig.add_scatter(x=predictions_short_target_teste['time'], y=predictions_short_target_teste['Label'], mode='markers', marker_color='rgba(255, 0, 0, .8)')

#fig.add_scatter(x=predictions_df_teste['time'], y=predictions_df_teste['baixa'], mode='markers', marker_color='rgba(255, 0, 0, .8)')

ymin=predictions_df_teste.close.min()
ymax=predictions_df_teste.close.max()
fig.update_yaxes(range=[ymin, ymax])

fig.show()
fig.write_html('/content/drive/MyDrive/ColabNotebooks/datasets/trading/modelos/long_target_valid_et.html')

In [ ]:
!pip install bta-lib
!pip install bt
import btalib as bta

In [ ]:
predictions_df_teste.head()

In [ ]:
close = pd.DataFrame()
close['sinal'] = np.where(predictions_df_teste['Label']>=1,1,0)
close['sinal'] = pd.to_numeric(close['sinal'])
close.set_index(predictions_df_teste.time, inplace=True)
close.fillna(0)
#close.value_counts()

venda = pd.DataFrame()
venda['sinal'] =np.where(predictions_short_target_teste['Label']>=1,-1,0)
venda['sinal'] = pd.to_numeric(venda['sinal'])
venda.fillna(0)
#venda.value_counts()

posicao = venda.copy()
posicao['sinal'] = 0
posicao[close.values == 1] = 1.0
posicao[venda.values == -1] = -1.0
posicao.set_index(predictions_df_teste.time, inplace=True)
posicao['sinal'].fillna(0)
posicao.value_counts()

sinal
 0       670
-1        44
 1         6
dtype: int64

In [ ]:
close = pd.DataFrame()
close['sinal'] = predictions_df_teste['close']
close.set_index(predictions_df_teste.time, inplace=True)

#3. Criar estrutura de backtesting

In [ ]:
#https://pmorissette.github.io/bt/
#https://colab.research.google.com/drive/1K56P-z6RK01tLYSvfRVadxQGKUp7h7VO?usp=sharing#scrollTo=EepGT0mwt6ou

In [ ]:
# download data
# calculate moving average DataFrame using pandas' rolling_mean
# a rolling mean is a moving average, right?
#sma = df_train.close.rolling(5).mean()

In [ ]:
import bt
et_strategy = bt.Strategy('et_strategy', [bt.algos.WeighTarget(posicao),
                                bt.algos.Rebalance()])

et_teste = bt.Backtest(et_strategy, close)
resultado = bt.run(et_teste)
#resultado.display()
#resultado.plot()
#resultado.plot_weights('et_strategy')

In [ ]:
s1 = bt.Strategy('s1', [bt.algos.SelectAll(),
                        bt.algos.WeighTarget(posicao),
                        bt.algos.Rebalance()])

s1_teste = bt.Backtest(s1, close, initial_capital=1000)
#, commissions=0.1)
                 #integer_positions=integer_positions)

res = bt.run(s1_teste)
#res.display()
#res.plot()
#res.plot_weights('s1')

In [ ]:
resultado.plot()

In [ ]:
resultado.plot_histogram()

In [ ]:
resultado.plot_security_weights()

In [ ]:
# create our new strategy
s2 = bt.Strategy('s2', [bt.algos.RunDaily(),
                        bt.algos.SelectAll(),
                        bt.algos.WeighInvVol(),
                        bt.algos.Rebalance()])

# now let's test it with the same data set. We will also compare it with our first backtest.
s2_teste = bt.Backtest(s2, close)
# we include test here to see the results side-by-side
resultado2 = bt.run(s1_teste, s2_teste)
#resultado2.display()

In [ ]:
resultado2.plot()

In [ ]:

btc_close = pd.DataFrame()
btc_close['sinal'] = predictions_df_teste['close']

btc_close.set_index(predictions_df_teste['time'], inplace=True)
btc_bands = bta.bbands(btc_close, period=20, devs=2.0).df
btc_up = pd.DataFrame()
btc_down = pd.DataFrame()

btc_down['sinal'] = btc_bands['bot']
btc_up['sinal'] =btc_bands['top']
btc_down['sinal'] = pd.to_numeric(btc_down['sinal'])
btc_up['sinal'] = pd.to_numeric(btc_up['sinal'])

btc_down.fillna(0)
btc_up.fillna(0)

posicao2 = btc_up.copy()
posicao2['sinal'] = 0

posicao2[btc_close > btc_up] = -1.0
posicao2[btc_close <= btc_down] = 1.0
posicao2['sinal'].fillna(0)

bbands = bt.Strategy('bbands', [bt.algos.WeighTarget(posicao2),
                                bt.algos.Rebalance()])

bteste = bt.Backtest(bbands, btc_close)

resultado2 = bt.run(bteste)
#resultado2.display()
#resultado2.plot()
#resultado2.plot_weights('bbands')

mm50 = pd.DataFrame()
mmm200 = pd.DataFrame()
mm50 = bta.sma(btc_close.sinal, period=50).df
mm200 = bta.sma(btc_close.sinal, period=200).df
mm50['sinal'] = mm50
mm200['sinal'] =mm200
posicao_2 = btc_up.copy()
posicao_2['sinal'] =0
posicao_2[mm50 > mm200] = 1.0
posicao_2[mm50 <=mm200] = -1.0
posicao_2.fillna(0)
mmovel = bt.Strategy('mmovel', [bt.algos.WeighTarget(posicao_2),
                                bt.algos.Rebalance()])

teste_sma = bt.Backtest(mmovel, btc_close)

benchmark = bt.Strategy('benchmark', [bt.algos.RunYearly(),
                                      bt.algos.SelectAll(),
                                      bt.algos.WeighEqually(),
                                      bt.algos.Rebalance()])

benchmark_teste = bt.Backtest(benchmark, btc_close)
b_resultado = bt.run(et_teste, bteste, teste_sma, benchmark_teste)
b_resultado.display()

Stat                 et_strategy    bbands      mmovel      benchmark
-------------------  -------------  ----------  ----------  -----------
Start                2021-09-13     2021-09-13  2021-09-13  2021-09-13
End                  2021-10-26     2021-10-26  2021-10-26  2021-10-26
Risk-free rate       0.00%          0.00%       0.00%       0.00%

Total Return         0.29%          -0.14%      1.36%       -1.73%
Daily Sharpe         1.58           -0.47       3.10        -3.39
Daily Sortino        2.76           -0.58       5.52        -5.12
CAGR                 2.49%          -1.15%      12.17%      -13.77%
Max Drawdown         -0.49%         -0.84%      -0.57%      -2.42%
Calmar Ratio         5.06           -1.37       21.37       -5.70

MTD                  0.09%          -0.01%      -0.01%      0.23%
3m                   -              -           -           -
6m                   -              -           -           -
YTD                  0.29%          -0.14%      1.36%     

In [ ]:
b_resultado.plot()

In [ ]:
#finalize a model
final_model = finalize_model(model_tuned)

In [ ]:
df_result = pd.DataFrame(b_resultado)

ValueError: ignored

In [ ]:
model_tuned

ExtraTreesClassifier(bootstrap=False, ccp_alpha=0.0,
                     class_weight='balanced_subsample', criterion='gini',
                     max_depth=6, max_features=1.0, max_leaf_nodes=None,
                     max_samples=None, min_impurity_decrease=0,
                     min_impurity_split=None, min_samples_leaf=4,
                     min_samples_split=7, min_weight_fraction_leaf=0.0,
                     n_estimators=200, n_jobs=-1, oob_score=False,
                     random_state=123, verbose=0, warm_start=False)